In [1]:
import yaml
from bartiq import Routine, compile_routine, evaluate, sympy_backend
from bartiq.analysis.explorer import Contributions

In [2]:
with open("tests/compilation/data/df_qref.yaml") as f:
    routine = Routine.from_qref(yaml.safe_load(f), sympy_backend)

# Expanded resources routine - gnarly
expanded = evaluate(compile_routine(routine).routine, {}).routine

# Unexpanded resources - not gnarly
unexpanded = compile_routine(routine).routine

In [35]:
# You can call .step_into(child_name) on this object directly, it'll be updated in place
Contributions(unexpanded, "active_volume")  # .step_into("LCU_compute_0")

# In the future, I want a `.evaluate(child_name)` function that
# evaluates only a part of an exptression - best of both worlds

Contributions(compiled_routine=CompiledRoutine(name='root', type='root', children={'qubits_alloc_0': CompiledRoutine(name='qubits_alloc_0', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=ceiling(log2(R + 1)))}, resources={}, connections={}, repetition=None, constraints=(), children_order=(), input_params=['M_r', 'N_spatial', 'R', 'b_as', 'b_givens', 'b_mas', 'idx']), 'qubits_alloc_1': CompiledRoutine(name='qubits_alloc_1', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=ceiling(log2(R)))}, resources={}, connections={}, repetition=None, constraints=(), children_order=(), input_params=['M_r', 'N_spatial', 'R', 'b_as', 'b_givens', 'b_mas', 'idx']), 'qubits_alloc_2': CompiledRoutine(name='qubits_alloc_2', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=1)}, resources={}, connections={}, repetition=None, constraints=(), children_order=(), input_params=['

In [ ]:
Contributions(expanded, "active_volume")

Contributions(compiled_routine=CompiledRoutine(name='root', type='root', children={'qubits_alloc_0': CompiledRoutine(name='qubits_alloc_0', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=ceiling(log2(R + 1)))}, resources={}, connections={}, repetition=None, constraints=(), children_order=(), input_params=['M_r', 'N_spatial', 'R', 'b_as', 'b_givens', 'b_mas', 'idx']), 'qubits_alloc_1': CompiledRoutine(name='qubits_alloc_1', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=ceiling(log2(R)))}, resources={}, connections={}, repetition=None, constraints=(), children_order=(), input_params=['M_r', 'N_spatial', 'R', 'b_as', 'b_givens', 'b_mas', 'idx']), 'qubits_alloc_2': CompiledRoutine(name='qubits_alloc_2', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=1)}, resources={}, connections={}, repetition=None, constraints=(), children_order=(), input_params=['

In [10]:
from bartiq.analysis import sympy_rewriter
from bartiq.analysis.rewriters.routine_rewriter import rewrite_routine_resources

rewriter = (
    sympy_rewriter(expanded.resource_values["active_volume"])
    .substitute("max(0, $x)", "0")
    .substitute("max(b_as, b_givens, b_mas)", "b_as")
    .substitute("mod(1, $x)", "x")
    .substitute("min(2, $x)", "2")
    .assume("b_as>5")
    .assume("log2(R) > 5")
    .substitute("ceiling($y)", "y")
    .substitute("R", "100")
)

new_routine = rewrite_routine_resources(expanded, "active_volume", instructions=rewriter.history())

In [ ]:
from bartiq import evaluate

Contributions(new_routine, "active_volume").step_into("LCU_compute_0").step_into(
    "DoubleFactorizationSelect_compute_0"
).step_into("DataLookupClean_compute_0")

Contributions(compiled_routine=CompiledRoutine(name='DataLookupClean_compute_0', type='qubrick', children={'qubits_alloc_0': CompiledRoutine(name='qubits_alloc_0', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=ceiling(log2(99*2**(ceiling(log2(M_r)) + 1)*M_r + 2**(ceiling(log2(M_r)) + ceiling(log2(99*M_r)) + 1)*(2**(b_mas + 1) - 1) + 2*M_r + 1)))}, resources={}, connections={}, repetition=None, constraints=(), children_order=(), input_params=['M_r', 'N_spatial', 'b_as', 'b_givens', 'b_mas', 'idx']), 'qubits_alloc_1': CompiledRoutine(name='qubits_alloc_1', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=(calc_lambda(100, ceiling(log2(99*2**(ceiling(log2(M_r)) + 1)*M_r + 2**(ceiling(log2(M_r)) + ceiling(log2(99*M_r)) + 1)*(2**(b_mas + 1) - 1) + 2*M_r + 1))) - 1)*ceiling(log2(99*2**(ceiling(log2(M_r)) + 1)*M_r + 2**(ceiling(log2(M_r)) + ceiling(log2(99*M_r)) + 1)*(2**(b_mas + 1) - 1) + 2*M_r + 1))

In [ ]:
# Poor integration at the moment, but in principle you can use a `ResourceRewriter` here
# with a number of different assumptions on it, call `apply_to_whole_routine()` and then `step_into` on
# that new routine object.

# This cell can be slow!

Contributions(
    ResourceRewriter(expanded, "active_volume")
    .substitute("max(0, $x)", "0")
    .substitute("max(b_as, b_givens, b_mas)", "b_as")
    .substitute("mod(1, $x)", "x")
    .substitute("min(2, $x)", "2")
    .assume("b_as>5")
    .assume("log2(R) > 5")
    .substitute("ceiling($y)", "y")  # Add any other substitutions / assumptions here before .apply_to_whole_routine
    .apply_to_whole_routine(),
    "active_volume",
).step_into("LCU_compute_0").step_into("DoubleFactorizationSelect_compute_0")

Contributions(compiled_routine=CompiledRoutine(name='DoubleFactorizationSelect_compute_0', type='qubrick', children={'DataLookupClean_compute_0': CompiledRoutine(name='DataLookupClean_compute_0', type='qubrick', children={'qubits_alloc_0': CompiledRoutine(name='qubits_alloc_0', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=ceiling(log2(2**(ceiling(log2(M_r)) + 1)*M_r*(R - 1) + 2**(ceiling(log2(M_r)) + ceiling(log2(M_r*(R - 1))) + 1)*(2**(b_mas + 1) - 1) + 2*M_r + 1)))}, resources={}, connections={}, repetition=None, constraints=(), children_order=(), input_params=['M_r', 'N_spatial', 'R', 'b_as', 'b_givens', 'b_mas', 'idx']), 'qubits_alloc_1': CompiledRoutine(name='qubits_alloc_1', type='qubits_alloc', children={}, ports={'out_0': Port(name='out_0', direction='output', size=(calc_lambda(R, ceiling(log2(2**(ceiling(log2(M_r)) + 1)*M_r*(R - 1) + 2**(ceiling(log2(M_r)) + ceiling(log2(M_r*(R - 1))) + 1)*(2**(b_mas + 1) - 1) + 2*M_r + 1))) - 1